## UPDATE: The second time I scraped also flood extent data from the Copernicus API since we couldn't use the summary tables we scraped initially due to errors that were later confirmed by Copernicus. It worked but later decided to **manually extract flood extents** from the Copernicus Viewer pages. This allowed me to **select the highest recorded extent** across all available products (observations), regardless of which product was used for the rest of the statistical data. This ensures the true extent of the each flood.

In [6]:
import pandas as pd
import requests
import time
import numpy as np
from tqdm import tqdm
import json 
from datetime import datetime

events = ['EMSR775', 'EMSR773', 'EMSR771', 'EMSR770', 'EMSR768', 'EMSR766', 'EMSR764', 'EMSR763', 'EMSR762', 'EMSR761', 'EMSR759',
          'EMSR758', 'EMSR757', 'EMSR756', 'EMSR755', 'EMSR728', 'EMSR725', 'EMSR722', 'EMSR721', 'EMSR718', 'EMSR713', 'EMSR712',
          'EMSR711', 'EMSR710', 'EMSR708', 'EMSR706', 'EMSR705', 'EMSR701', 'EMSR697', 'EMSR694', 'EMSR693', 'EMSR692', 'EMSR684',
          'EMSR683', 'EMSR680', 'EMSR668', 'EMSR665', 'EMSR664', 'EMSR659', 'EMSR657']

products_data = []

for event in tqdm(events):
    url = f'https://rapidmapping.emergency.copernicus.eu/backend/dashboard-api/public-activations/?format=json&code={event}'
    response = requests.get(url)
    time.sleep(5)  # IMPORTANT
    data = response.json()
    
    aois = data['results'][0]['aois'] 
    if aois:
        for aoi in aois:
            aois_data_generic = {
                "name": aoi.get("name", np.nan),
                "number": aoi.get("number", np.nan),
                "activationCode": aoi.get("activationCode", np.nan)
            }
        
            products = aoi.get('products', [])
            if products:
                for product in products:
                    # Add product-specific information
                    aois_data_products = {
                        "activation_code": product.get("activationCode", np.nan),
                        "aoiName": product.get("aoiName", np.nan),
                        "aoiNumber": product.get("aoiNumber", np.nan),
                        "type": product.get("type", np.nan),
                        "monitoring": product.get("monitoringNumber", np.nan),
                    }
    
                    version = product.get('version') if 'version' in product else None
                    version_data = {
                        "deliveryTime": version.get("deliveryTime", np.nan) if version else np.nan
                    }
        
                    # Check if 'stats' exists, if not, prepare for a row with empty or NaN stats data
                    stats = product.get('stats')
                    if stats:
                        # If 'stats' is available, loop through it
                        for category, subcategories in stats.items():
                            if isinstance(subcategories, dict):  # If subcategories is a dictionary
                                for subcategory, values in subcategories.items():
                                    subcategory_unit = f"{category}_{subcategory}_({values.get('unit', np.nan)})"
                                    affected = values.get('affected', np.nan)
                                    total = values.get('total', np.nan)
                                    
                                    product_stat_all = {
                                        "name": aois_data_generic["name"],
                                        "number": aois_data_generic["number"],
                                        "activationCode": aois_data_generic["activationCode"],
                                        "activation_code": aois_data_products["activation_code"],
                                        "aoiName": aois_data_products["aoiName"],
                                        "aoiNumber": aois_data_products["aoiNumber"],
                                        "type": aois_data_products["type"],
                                        "monitoring": aois_data_products["monitoring"],
                                        "deliveryTime": version_data["deliveryTime"],                                    
                                        "subcategory_unit": subcategory_unit,
                                        "affected": affected,
                                        "total": total
                                    }
                                    products_data.append(product_stat_all)
                            else:
                                print(f"  Subcategory info is not a dict, found: {type(subcategories)}")
                    else:
                        # If 'stats' is not available, still add the row with NaN for affected and subcategory_unit
                        product_stat_all = {
                            "name": aois_data_generic["name"],
                            "number": aois_data_generic["number"],
                            "activationCode": aois_data_generic["activationCode"],
                            "activation_code": aois_data_products["activation_code"],
                            "aoiName": aois_data_products["aoiName"],
                            "aoiNumber": aois_data_products["aoiNumber"],
                            "type": aois_data_products["type"],
                            "monitoring": aois_data_products["monitoring"],
                            "deliveryTime": version_data["deliveryTime"],                                    
                            "subcategory_unit": np.nan,  # Set this to NaN because no stats info
                            "affected": np.nan,  # Set affected to NaN as there are no stats to extract
                            "total": np.nan
                        }
                        products_data.append(product_stat_all)

# Convert the data to a DataFrame for further use
aois_df_2 = pd.DataFrame(products_data)
aois_df_2

100%|██████████████████| 40/40 [04:24<00:00,  6.62s/it]


name  number activationCode activation_code  \
0                       Olden       1        EMSR775         EMSR775   
1                       Oyane       2        EMSR775         EMSR775   
2                       Oyane       2        EMSR775         EMSR775   
3              Aurlandsvangen       3        EMSR775         EMSR775   
4                  Over Ardal       4        EMSR775         EMSR775   
5                        Voss       5        EMSR775         EMSR775   
6                       Sauda       6        EMSR775         EMSR775   
7                Ardalstangen       7        EMSR775         EMSR775   
8                      Gaupne       8        EMSR775         EMSR775   
9                      Fardal       9        EMSR775         EMSR775   
10               Vetlefjorden      10        EMSR775         EMSR775   
11                  Viksdalen      11        EMSR775         EMSR775   
12                  Viksdalen      11        EMSR775         EMSR775   
13                  Viksdalen      11        EMSR775         EMSR775   
14                  Viksdalen      11        EMSR775         EMSR775   
15                  Viksdalen      11        EMSR775         EMSR775   
16                       Odda      12        EMSR775         EMSR775   
17                 Omastranda      13        EMSR775         EMSR775   
18                    Vadheim      14        EMSR775         EMSR775   
19          Valencia province       1        EMSR773         EMSR773   
20          Valencia province       1        EMSR773         EMSR773   
21          Valencia province       1        EMSR773         EMSR773   
22          Valencia province       1        EMSR773         EMSR773   
23          Valencia province       1        EMSR773         EMSR773   
24          Valencia province       1        EMSR773         EMSR773   
25          Valencia province       1        EMSR773         EMSR773   
26          Valencia province       1        EMSR773         EMSR773   
27          Valencia province       1        EMSR773         EMSR773   
28          Valencia province       1        EMSR773         EMSR773   
29          Valencia province       1        EMSR773         EMSR773   
30          Valencia province       1        EMSR773         EMSR773   
31          Valencia province       1        EMSR773         EMSR773   
32          Valencia province       1        EMSR773         EMSR773   
33          Valencia province       1        EMSR773         EMSR773   
34          Valencia province       1        EMSR773         EMSR773   
35          Valencia province       1        EMSR773         EMSR773   
36          Valencia province       1        EMSR773         EMSR773   
37          Valencia province       1        EMSR773         EMSR773   
38          Valencia province       1        EMSR773         EMSR773   
39          Valencia province       1        EMSR773         EMSR773   
40          Valencia province       1        EMSR773         EMSR773   
41          Valencia province       1        EMSR773         EMSR773   
42          Valencia province       1        EMSR773         EMSR773   
43          Valencia province       1        EMSR773         EMSR773   
44          Valencia province       1        EMSR773         EMSR773   
45          Valencia province       1        EMSR773         EMSR773   
46          Valencia province       1        EMSR773         EMSR773   
47          Valencia province       1        EMSR773         EMSR773   
48          Valencia province       1        EMSR773         EMSR773   
49          Valencia province       1        EMSR773         EMSR773   
50          Valencia province       1        EMSR773         EMSR773   
51          Valencia province       1        EMSR773         EMSR773   
52          Valencia province       1        EMSR773         EMSR773   
53          Valencia province       1        EMSR773         EMSR773   
54          Valencia province       1        EMSR773         EMSR

In [3]:
pd.set_option("display.max.rows", None)
aois_df_2

name  number activationCode activation_code  \
0                     Olden       1        EMSR775         EMSR775   
1                     Oyane       2        EMSR775         EMSR775   
2                     Oyane       2        EMSR775         EMSR775   
3            Aurlandsvangen       3        EMSR775         EMSR775   
4                Over Ardal       4        EMSR775         EMSR775   
5                      Voss       5        EMSR775         EMSR775   
6                     Sauda       6        EMSR775         EMSR775   
7              Ardalstangen       7        EMSR775         EMSR775   
8                    Gaupne       8        EMSR775         EMSR775   
9                    Fardal       9        EMSR775         EMSR775   
10             Vetlefjorden      10        EMSR775         EMSR775   
11                Viksdalen      11        EMSR775         EMSR775   
12                Viksdalen      11        EMSR775         EMSR775   
13                Viksdalen      11        EMSR775         EMSR775   
14                Viksdalen      11        EMSR775         EMSR775   
15                Viksdalen      11        EMSR775         EMSR775   
16                     Odda      12        EMSR775         EMSR775   
17               Omastranda      13        EMSR775         EMSR775   
18                  Vadheim      14        EMSR775         EMSR775   
19        Valencia province       1        EMSR773         EMSR773   
20        Valencia province       1        EMSR773         EMSR773   
21        Valencia province       1        EMSR773         EMSR773   
22        Valencia province       1        EMSR773         EMSR773   
23        Valencia province       1        EMSR773         EMSR773   
24        Valencia province       1        EMSR773         EMSR773   
25        Valencia province       1        EMSR773         EMSR773   
26        Valencia province       1        EMSR773         EMSR773   
27        Valencia province       1        EMSR773         EMSR773   
28        Valencia province       1        EMSR773         EMSR773   
29        Valencia province       1        EMSR773         EMSR773   
30        Valencia province       1        EMSR773         EMSR773   
31        Valencia province       1        EMSR773         EMSR773   
32        Valencia province       1        EMSR773         EMSR773   
33        Valencia province       1        EMSR773         EMSR773   
34        Valencia province       1        EMSR773         EMSR773   
35        Valencia province       1        EMSR773         EMSR773   
36        Valencia province       1        EMSR773         EMSR773   
37        Valencia province       1        EMSR773         EMSR773   
38        Valencia province       1        EMSR773         EMSR773   
39        Valencia province       1        EMSR773         EMSR773   
40        Valencia province       1        EMSR773         EMSR773   
41        Valencia province       1        EMSR773         EMSR773   
42        Valencia province       1        EMSR773         EMSR773   
43        Valencia province       1        EMSR773         EMSR773   
44        Valencia province       1        EMSR773         EMSR773   
45        Valencia province       1        EMSR773         EMSR773   
46        Valencia province       1        EMSR773         EMSR773   
47        Valencia province       1        EMSR773         EMSR773   
48        Valencia province       1        EMSR773         EMSR773   
49        Valencia province       1        EMSR773         EMSR773   
50        Valencia province       1        EMSR773         EMSR773   
51        Valencia province       1        EMSR773         EMSR773   
52        Valencia province       1        EMSR773         EMSR773   
53        Valencia province       1        EMSR773         EMSR773   
54        Valencia province       1        EMSR773         EMSR773   
55        Valencia province       1        EMSR773         EMSR773   
56        Valencia province      

In [7]:
aois_df_2.to_excel("new_aois_df_2.xlsx", index=False)

# ANOTHER SCRAPING AFTER COPERNICUS CORRECTED THEIR DATA UPON OUR COMMONUCATION

#### 15 February 2025

In [1]:
import pandas as pd
import requests
import time
import numpy as np
from tqdm import tqdm
import json 
from datetime import datetime

events = ['EMSR775', 'EMSR773', 'EMSR771', 'EMSR770', 'EMSR768', 'EMSR766', 'EMSR764', 'EMSR763', 'EMSR762', 'EMSR761', 'EMSR759',
          'EMSR758', 'EMSR757', 'EMSR756', 'EMSR755', 'EMSR728', 'EMSR725', 'EMSR722', 'EMSR721', 'EMSR718', 'EMSR713', 'EMSR712',
          'EMSR711', 'EMSR710', 'EMSR708', 'EMSR706', 'EMSR705', 'EMSR701', 'EMSR697', 'EMSR694', 'EMSR693', 'EMSR692', 'EMSR684',
          'EMSR683', 'EMSR680', 'EMSR668', 'EMSR665', 'EMSR664', 'EMSR659', 'EMSR657']

products_data = []

for event in tqdm(events):
    url = f'https://rapidmapping.emergency.copernicus.eu/backend/dashboard-api/public-activations/?format=json&code={event}'
    response = requests.get(url)
    time.sleep(5)  # IMPORTANT
    data = response.json()
    
    aois = data['results'][0]['aois'] 
    if aois:
        for aoi in aois:
            aois_data_generic = {
                "name": aoi.get("name", np.nan),
                "number": aoi.get("number", np.nan),
                "activationCode": aoi.get("activationCode", np.nan)
            }
        
            products = aoi.get('products', [])
            if products:
                for product in products:
                    # Add product-specific information
                    aois_data_products = {
                        "activation_code": product.get("activationCode", np.nan),
                        "aoiName": product.get("aoiName", np.nan),
                        "aoiNumber": product.get("aoiNumber", np.nan),
                        "type": product.get("type", np.nan),
                        "monitoring": product.get("monitoringNumber", np.nan),
                    }
    
                    version = product.get('version') if 'version' in product else None
                    version_data = {
                        "deliveryTime": version.get("deliveryTime", np.nan) if version else np.nan
                    }
        
                    # Check if 'stats' exists, if not, prepare for a row with empty or NaN stats data
                    stats = product.get('stats')
                    if stats:
                        # If 'stats' is available, loop through it
                        for category, subcategories in stats.items():
                            if isinstance(subcategories, dict):  # If subcategories is a dictionary
                                for subcategory, values in subcategories.items():
                                    subcategory_unit = f"{category}_{subcategory}_({values.get('unit', np.nan)})"
                                    affected = values.get('affected', np.nan)
                                    total = values.get('total', np.nan)
                                    
                                    product_stat_all = {
                                        "name": aois_data_generic["name"],
                                        "number": aois_data_generic["number"],
                                        "activationCode": aois_data_generic["activationCode"],
                                        "activation_code": aois_data_products["activation_code"],
                                        "aoiName": aois_data_products["aoiName"],
                                        "aoiNumber": aois_data_products["aoiNumber"],
                                        "type": aois_data_products["type"],
                                        "monitoring": aois_data_products["monitoring"],
                                        "deliveryTime": version_data["deliveryTime"],                                    
                                        "subcategory_unit": subcategory_unit,
                                        "affected": affected,
                                        "total": total
                                    }
                                    products_data.append(product_stat_all)
                            else:
                                print(f"  Subcategory info is not a dict, found: {type(subcategories)}")
                    else:
                        # If 'stats' is not available, still add the row with NaN for affected and subcategory_unit
                        product_stat_all = {
                            "name": aois_data_generic["name"],
                            "number": aois_data_generic["number"],
                            "activationCode": aois_data_generic["activationCode"],
                            "activation_code": aois_data_products["activation_code"],
                            "aoiName": aois_data_products["aoiName"],
                            "aoiNumber": aois_data_products["aoiNumber"],
                            "type": aois_data_products["type"],
                            "monitoring": aois_data_products["monitoring"],
                            "deliveryTime": version_data["deliveryTime"],                                    
                            "subcategory_unit": np.nan,  # Set this to NaN because no stats info
                            "affected": np.nan,  # Set affected to NaN as there are no stats to extract
                            "total": np.nan
                        }
                        products_data.append(product_stat_all)

# Convert the data to a DataFrame for further use
aois_df_3 = pd.DataFrame(products_data)
aois_df_3

100%|██████████████████| 40/40 [04:21<00:00,  6.54s/it]


name  number activationCode activation_code         aoiName  \
0              Olden       1        EMSR775         EMSR775           Olden   
1              Oyane       2        EMSR775         EMSR775           Oyane   
2              Oyane       2        EMSR775         EMSR775           Oyane   
3     Aurlandsvangen       3        EMSR775         EMSR775  Aurlandsvangen   
4         Over Ardal       4        EMSR775         EMSR775      Over Ardal   
...              ...     ...            ...             ...             ...   
7666    DaugavaRiver       1        EMSR657         EMSR657    DaugavaRiver   
7667    DaugavaRiver       1        EMSR657         EMSR657    DaugavaRiver   
7668    DaugavaRiver       1        EMSR657         EMSR657    DaugavaRiver   
7669    DaugavaRiver       1        EMSR657         EMSR657    DaugavaRiver   
7670    DaugavaRiver       1        EMSR657         EMSR657    DaugavaRiver   

      aoiNumber type  monitoring         deliveryTime  \
0             1  DEL           0  2024-11-01T14:12:00   
1             2  DEL           0  2024-11-01T18:30:00   
2             2  DEL           1                 None   
3             3  DEL           0  2024-11-01T17:25:00   
4             4  DEL           0  2024-11-01T20:43:00   
...         ...  ...         ...                  ...   
7666          1  DEL           5  2023-04-06T18:59:00   
7667          1  DEL           5  2023-04-06T18:59:00   
7668          1  DEL           5  2023-04-06T18:59:00   
7669          1  DEL           5  2023-04-06T18:59:00   
7670          1  DEL           5  2023-04-06T18:59:00   

                                subcategory_unit  affected    total  
0                                            NaN       NaN      NaN  
1                                            NaN       NaN      NaN  
2                                            NaN       NaN      NaN  
3                                            NaN       NaN      NaN  
4                                            NaN       NaN      NaN  
...                                          ...       ...      ...  
7666          Transportation_Secondary Road_(km)       8.0    207.7  
7667        Transportation_Airfield runways_(km)       0.9     12.4  
7668  Transportation_Long-distance railways_(km)       0.5    316.6  
7669                Estimated population_None_()     300.0  83000.0  
7670             Previous flooded area_None_(ha)       NaN   5485.1  

[7671 rows x 12 columns]

In [2]:
aois_df_3.to_excel("final_scraped_data.xlsx", index=False)